# SQLite

![SQLite](https://upload.wikimedia.org/wikipedia/commons/3/38/SQLite370.svg)

## SQLite

SQL: structured query language for relational databases

* SQLite implements a simple SQL dialect
* SQLite uses data files
  * No need to setup a database server
* Widely used and supported, e.g. on mobile phones

## SQLite Interactive

* SQLite has a SQL interactive tool
  * Please download from: http://www.sqlite.org/download.html
  * Guide to SQLite interpreter: http://sqlite.org/cli.html

## SQLite Interactive

1. Download and install SQLite
2. Go to your Terminal or Command Line, and enter: 

```shell
sqlite3
```
3. Start using SQLite interactive with 
    + dot commands
    + SQL statements

Here is the interface on the Mac terminal / command line: 

<img src="figures/sqlite3.png" style="width:700px" alt="sqlite">

Enter ```.help``` (a dot command) on SQLite prompt will list all supported commands. 
```shell
sqlite> .help
```

### Load SQL Magic

In [2]:
%load_ext sql

The sql extension is already loaded. To reload it, use:
  %reload_ext sql


## Database ```college.db```

Suppose we are to manage the following data in a college: 
1. Degree programs with ID, program name, and description
2. Students in the programs, with: ID, name, program information, and class year. 

### Load SQLite Database

In [3]:
%sql sqlite:///college.db

Let's open -- create if it does not exist -- a database file called ```college.db```: 

```shell
sqlite> .open college.db
``` 

Screenshot on Mac terminal: 

<img src="figures/sqlite_open.png" style="width:700px" alt="sqlite">

We can now create the two tables using SQL statements with the SQLite3 interactive. 

Please note that ```%%sql``` symbols, for example: 

In [ ]:
%%sql
select * from my_table;

in this tutorial is for SQL magic in the Jupyter Notebook and should **be excluded** from your actual SQL statement. 

### ```programs``` table

Create the ```programs``` table structure: 

In [36]:
%%sql
drop table if exists programs;
create table programs (
    program_id varchar(10) not null primary key, 
    program_name varchar(20), 
    program_desc varchar(500)
);

 * sqlite:///college.db
Done.
Done.


[]

Now add (insert) program data: 

In [37]:
%%sql
insert into programs (program_id, program_name, program_desc)
            values   ('IS', "Information Systems", "Information systems with a business angle");
insert into programs values ('DS', "Data Science", "New data science program");
insert into programs values 
        ('CS', "Computer Science", "Traditional computer science"),
        ('CST', "Computing & Security Technology", "CST with a new focus on security");

 * sqlite:///college.db
1 rows affected.
1 rows affected.
2 rows affected.


[]

Now let's take a look at data in the table: 

In [14]:
%%sql
select * from programs;

 * sqlite:///college.db
Done.


[('IS', 'Information Systems', 'Information systems with a business angle'),
 ('DS', 'Data Science', 'New data science program'),
 ('CS', 'Computer Science', 'Traditional computer science'),
 ('CST', 'Computing & Security Technology', 'CST with a new focus on security')]

### ```students``` table

Create the students table: 

In [19]:
%%sql
drop table if exists students;
create table students (
    student_id integer primary key, 
    student_name varchar(100), 
    program_id varchar(10),
    class_year int
);

 * sqlite:///college.db
Done.
Done.


[]

For the students tables, we have preppared a csv file with students records, which can be downloaded from: [students.csv](data/students.csv). 

Suppose data file ```students.csv``` is in the **same directory as the college.db**: 

```csv
1	John Smith,        IS,  2020
2	Albert Einstein,   DS	2021
3	George Washington, CS,  2019
4	Donald Trump,      CST, 2020
5	Barack Obama,      IS,  2021
.   ...                ..   ....
```

You can use the following **dot commands** to import the CSV data: 

```shell
sqlite> .mode csv
sqlite> .import students.csv students
```

Now check out the data: 

In [21]:
%%sql
select * from students limit 5;

 * sqlite:///college.db
Done.


[(1, 'John Smith', 'IS', 2020),
 (2, 'Albert Einstein', 'DS', 2021),
 (3, 'George Washington', 'CS', 2019),
 (4, 'Donald Trump', 'CST', 2020),
 (5, 'Barack Obama', 'IS', 2021)]

In [23]:
%%sql
select count(*) from students;

 * sqlite:///college.db
Done.


[(50,)]

### Select and Filter

Now that we have the data, we can go ahead to search the data and run statistics. 

For example, if you are interested in students in the DS program: 

In [28]:
%%sql
select * from students where program_id='DS';

 * sqlite:///college.db
Done.


[(2, 'Albert Einstein', 'DS', 2021),
 (6, 'Mark Twain', 'DS', 2020),
 (8, 'Kanye West', 'DS', 2040),
 (13, 'SpongeBob', 'DS', 2023),
 (14, 'Jackob Ziv', 'DS', 2020),
 (39, 'Spiderman', 'DS', 2030),
 (40, 'Harambe Noll', 'DS', 2020),
 (43, 'Johnny Bravo', 'DS', 2022)]

Or, you would like to know who have graduated before 2019: 

In [30]:
%%sql
select * from students where class_year<2019;

 * sqlite:///college.db
Done.


[(9, 'Felix Monika', 'CST', 2012),
 (10, 'Noble Pearl', 'IS', 2015),
 (11, 'Linus Torvalds', 'CS', 2016),
 (18, 'Josh Brolin', 'CST', 2018),
 (23, 'Matt Murdoc', 'IT', 2018),
 (28, 'Keith Kogane', 'CS', 2018),
 (31, 'Claude Giroux', 'CST', 2018),
 (35, 'Bruce Char', 'CST', 2018),
 (49, 'John Fry', 'CS', 2010)]

### Group Aggregates

Perhaps, you only want to know statistics in each program: 

In [27]:
%%sql
select program_id, 
       count(*) as student_count, 
       min(class_year) as first_class, 
       max(class_year) as last_class
from students 
group by program_id
order by student_count DESC;

 * sqlite:///college.db
Done.


[('IS', 14, 2015, 2023),
 ('CST', 13, 2012, 2022),
 ('CS', 11, 2010, 2031),
 ('DS', 8, 2020, 2040),
 ('IT', 4, 2018, 2020)]

### Update Student Data

Now that you see from the statistics some data values are unrealistic such as a class year $>2030$. Perhaps we can reset all these values to $2030$ if they are greater than that:

In [ ]:
%%sql
update students set class_year = 2030 where class_year > 2030;

We can run the statistics again to see if data have been updated: 

In [38]:
%%sql
select program_id, 
       count(*) as student_count, 
       min(class_year) as first_class, 
       max(class_year) as last_class
from students 
group by program_id
order by student_count DESC;

 * sqlite:///college.db
Done.


[('IS', 14, 2015, 2023),
 ('CST', 13, 2012, 2022),
 ('CS', 11, 2010, 2030),
 ('DS', 8, 2020, 2030),
 ('IT', 4, 2018, 2020)]

### Join Tables

Suppose you want to retrieve student data with their corresponding program information (e.g. program name): 

In [39]:
%%sql
select student_name, program_name, class_year
from students s join programs p on s.program_id = p.program_id
limit 10;

 * sqlite:///college.db
Done.


[('John Smith', 'Information Systems', 2020),
 ('Albert Einstein', 'Data Science', 2021),
 ('George Washington', 'Computer Science', 2019),
 ('Donald Trump', 'Computing & Security Technology', 2020),
 ('Barack Obama', 'Information Systems', 2021),
 ('Mark Twain', 'Data Science', 2020),
 ('Joey Binzinger', 'Information Systems', 2023),
 ('Kanye West', 'Data Science', 2030),
 ('Felix Monika', 'Computing & Security Technology', 2012),
 ('Noble Pearl', 'Information Systems', 2015)]

We can rerun the previous statistics based on the program names, instead of program IDs: 

In [41]:
%%sql
select program_name, 
       count(*) as student_count, 
       min(class_year) as first_class, 
       max(class_year) as last_class
from students s join programs p on s.program_id = p.program_id
group by program_name
order by student_count DESC;

 * sqlite:///college.db
Done.


[('Information Systems', 14, 2015, 2023),
 ('Computing & Security Technology', 13, 2012, 2022),
 ('Computer Science', 11, 2010, 2030),
 ('Data Science', 8, 2020, 2030)]

# References

+ Chapter 3 Managing Data, section Managing Data using SQL, of LauraCasselland AlanGauld (2014). Python Projects.https://ebookcentral-proquest-com.ezproxy2.library.drexel.edu/lib/drexel-ebooks/detail.action?docID=1875898
+ SQLite operations in Python:http://sebastianraschka.com/Articles/2014_sqlite_in_python_tutorial.html

This is not the most efficient method to join and run the ```group by``` clause. But for now, it is good for the small dataset here. 